In [41]:
import numpy as np
import pandas as pd

import plotly.express as px
import plotly.figure_factory as ff
import plotly.graph_objects as go


from time import time
import numpy as np
import matplotlib.path as mpltPath

import math

In [2]:
folder="/home/spoudel/All_Thesis/Thesis_program/Data/shawnee/location_1/Kmeans/"

In [4]:
location_in_time=pd.read_csv(folder+"/location_in_time.csv")

In [5]:
location_in_time

Unnamed: 0                     Start                       End  passID  \
0           0  2023-01-16T17:24:39.000Z  2023-01-16T17:25:25.000Z     115   
1           1  2023-01-16T17:25:52.000Z  2023-01-16T17:26:38.000Z     117   
2           2  2023-01-16T17:27:08.000Z  2023-01-16T17:27:55.000Z     118   
3           3  2023-01-16T17:29:06.000Z  2023-01-16T17:29:53.000Z     120   
4           4  2023-01-16T17:30:23.000Z  2023-01-16T17:31:09.000Z     121   

     lat_min    lat_max   long_min   long_max  
0  35.670006  35.670785 -96.662316 -96.662305  
1  35.670014  35.670792 -96.662317 -96.662304  
2  35.670003  35.670800 -96.662341 -96.662327  
3  35.670000  35.670794 -96.662342 -96.662329  
4  35.670007  35.670784 -96.662333 -96.662319

In [6]:
passes=location_in_time["passID"].values
passes

array([115, 117, 118, 120, 121])

In [7]:
each_data=[pd.read_csv(folder+f"/cluster_predicted_pass_{x}.csv") for x in location_in_time["passID"]]

In [8]:
# Compute heading
def compute_heading(df):
    df["heading"] = 0
    for i in range(len(df) - 1):
        a = df.loc[i, "latitude"] - df.loc[i + 1, "latitude"]
        b = df.loc[i, "longitude"] - df.loc[i + 1, "longitude"]
        d = 180 / np.pi * np.arctan2(a, b) + 180
        df.loc[i, "heading"] = d

In [9]:
def projectRollerWidth(df_in, rollerWidth=6, nPoints=6):
    df=df_in.copy(deep=True)
    copyDF = df.copy()
    halfWidth = rollerWidth // 2
    for i in np.arange(-halfWidth, halfWidth, rollerWidth / nPoints):
        tmpDF = copyDF.copy()
        tmpDF.latitude = (
            np.sin(2 * np.pi / 360 * (copyDF.heading.values - 90)) * i / 3600 / 101
            + copyDF.latitude.values
        )
        tmpDF.longitude = (
            np.cos(2 * np.pi / 360 * (copyDF.heading.values - 90)) * i / 3600 / 80
            + copyDF.longitude.values
        )
        tmpDF.original = False
        df = df.append(tmpDF)
    df =df.sort_values("timestamp")
    return df

In [10]:
each_data_projected=[[]]*len(each_data)
for i in range(len(passes)):
    each_data[i]["pass_no"]=i
    length=len(each_data[i])
    latitudes = np.linspace(location_in_time["lat_min"][i],location_in_time["lat_max"][i] , num=length)
    print(len(latitudes))
    each_data[i]["latitude"]=latitudes
    longitudes= np.linspace(location_in_time["long_min"][i],location_in_time["long_max"][i] , num=length)
    each_data[i]["longitude"]=longitudes
    
    each_data[i]["prev"]=each_data[i]["cluster"].shift(1)
    each_data[i]["change"]=each_data[i].apply(lambda x: 1 if abs(x["prev"]-x["cluster"]>1)  else 0, axis=1)
       
    print(i)
    if i==0:
        each_data[i]["first"]=True
        each_data[i]["last"]=False
    elif i==len(passes)-1:
        each_data[i]["first"]=False
        each_data[i]["last"]=True
    else:
        each_data[i]["first"]=False
        each_data[i]["last"]=False
        
        
    compute_heading(each_data[i])
    each_data_projected[i]=projectRollerWidth(each_data[i])

        
full_data=pd.concat(each_data)
full_data=full_data[full_data["pass_no"]!=0]

full_data_projected=pd.concat(each_data_projected)
full_data_projected=full_data_projected[full_data_projected["pass_no"]!=0]

358
0
360
1
366
2


/tmp/ipykernel_597642/2125603734.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(tmpDF)
/tmp/ipykernel_597642/2125603734.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(tmpDF)
/tmp/ipykernel_597642/2125603734.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(tmpDF)
/tmp/ipykernel_597642/2125603734.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(tmpDF)
/tmp/ipykernel_597642/2125603734.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(tmpDF)
/tmp/ipykernel_

366
3
360
4


/tmp/ipykernel_597642/2125603734.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(tmpDF)
/tmp/ipykernel_597642/2125603734.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(tmpDF)
/tmp/ipykernel_597642/2125603734.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(tmpDF)
/tmp/ipykernel_597642/2125603734.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(tmpDF)


In [11]:
full_data["time"]=full_data["timestamp"]
full_data["passID"]=full_data["pass_no"]
full_data["speed"]=1.1
full_data["temperature"]=167.5

full_data["density"]=full_data["cluster"]
full_data.to_csv(folder+"/full_data_to_project.csv")
full_data

Unnamed: 0.1  Unnamed: 0                         timestamp  total_power  \
0               0           0  2023-01-16 17:25:52.120000+00:00   100.000000   
1               1           1  2023-01-16 17:25:52.257000+00:00    82.183425   
2               2           2  2023-01-16 17:25:52.384000+00:00    83.212034   
3               3           3  2023-01-16 17:25:52.511000+00:00    58.360112   
4               4           4  2023-01-16 17:25:52.638000+00:00    62.575446   
..            ...         ...                               ...          ...   
355           355         355  2023-01-16 17:31:08.215000+00:00    18.406951   
356           356         356  2023-01-16 17:31:08.342000+00:00    67.584552   
357           357         357  2023-01-16 17:31:08.469000+00:00    82.175854   
358           358         358  2023-01-16 17:31:08.596000+00:00   100.000000   
359           359         359  2023-01-16 17:31:08.723000+00:00    38.006939   

           p0        p1        p2        p3        p4        p5  ...  prev  \
0   -2.000000  2.000000  2.000000  0.935329  2.000000  2.000000  ...   NaN   
1   -2.000000 -0.085897 -0.100313  0.562901  1.384732  0.605973  ...   4.0   
2   -2.000000  0.909739 -0.090134  0.542970  0.487589  0.860677  ...   3.0   
3   -0.510243 -0.707589 -0.276745 -0.355957 -0.028058  0.654395  ...   0.0   
4    0.922105 -0.875624 -0.435802  0.125723 -0.576983  0.532818  ...   2.0   
..        ...       ...       ...       ...       ...       ...  ...   ...   
355  0.619154  2.000000 -0.067383 -0.711903 -0.299709 -0.395371  ...   4.0   
356  0.658804  0.218019 -0.212631 -0.182176  1.719183  1.880953  ...   2.0   
357  0.966712  0.201359  0.004933  2.000000  0.814174 -0.509651  ...   4.0   
358  1.250349 -0.648439  1.299200  2.000000 -0.037076 -0.079023  ...   3.0   
359  1.158490 -0.567994  0.230944  0.437043 -0.654288  0.330046  ...   3.0   

     change  first   last    heading                              time  \
0         0  False  False  89.042705  2023-01-16 17:25:52.120000+00:00   
1         0  False  False  89.042705  2023-01-16 17:25:52.257000+00:00   
2         1  False  False  89.042705  2023-01-16 17:25:52.384000+00:00   
3         0  False  False  89.042705  2023-01-16 17:25:52.511000+00:00   
4         0  False  False  89.042705  2023-01-16 17:25:52.638000+00:00   
..      ...    ...    ...        ...                               ...   
355       1  False   True  88.967755  2023-01-16 17:31:08.215000+00:00   
356       0  False   True  88.967755  2023-01-16 17:31:08.342000+00:00   
357       0  False   True  88.967755  2023-01-16 17:31:08.469000+00:00   
358       0  False   True  88.967755  2023-01-16 17:31:08.596000+00:00   
359       0  False   True   0.000000  2023-01-16 17:31:08.723000+00:00   

     passID  speed  temperature  density  
0         1    1.1        167.5        4  
1         1    1.1        167.5        3  
2         1    1.1        167.5        0  
3         1    1.1        167.5        2  
4         1    1.1        167.5        2  
..      ...    ...          ...      ...  
355       4    1.1        167.5        2  
356       4    1.1        167.5        4  
357       4    1.1        167.5        3  
358       4    1.1        167.5        3  
359       4    1.1        167.5        2  

[1452 rows x 25 columns]

In [14]:
full_data_projected["time"]=full_data_projected["timestamp"]
full_data_projected["passID"]=full_data_projected["pass_no"]

full_data_projected["speed"]=1.1
full_data_projected["temperature"]=167.5

full_data_projected["density"]=full_data_projected["cluster"]
full_data_projected

# full_data_projected.to_csv(folder+"full_data_projected.csv")

Unnamed: 0.1  Unnamed: 0                         timestamp  total_power  \
0               0           0  2023-01-16 17:25:52.120000+00:00   100.000000   
0               0           0  2023-01-16 17:25:52.120000+00:00   100.000000   
0               0           0  2023-01-16 17:25:52.120000+00:00   100.000000   
0               0           0  2023-01-16 17:25:52.120000+00:00   100.000000   
0               0           0  2023-01-16 17:25:52.120000+00:00   100.000000   
..            ...         ...                               ...          ...   
359           359         359  2023-01-16 17:31:08.723000+00:00    38.006939   
359           359         359  2023-01-16 17:31:08.723000+00:00    38.006939   
359           359         359  2023-01-16 17:31:08.723000+00:00    38.006939   
359           359         359  2023-01-16 17:31:08.723000+00:00    38.006939   
359           359         359  2023-01-16 17:31:08.723000+00:00    38.006939   

          p0        p1        p2        p3        p4        p5  ...  prev  \
0   -2.00000  2.000000  2.000000  0.935329  2.000000  2.000000  ...   NaN   
0   -2.00000  2.000000  2.000000  0.935329  2.000000  2.000000  ...   NaN   
0   -2.00000  2.000000  2.000000  0.935329  2.000000  2.000000  ...   NaN   
0   -2.00000  2.000000  2.000000  0.935329  2.000000  2.000000  ...   NaN   
0   -2.00000  2.000000  2.000000  0.935329  2.000000  2.000000  ...   NaN   
..       ...       ...       ...       ...       ...       ...  ...   ...   
359  1.15849 -0.567994  0.230944  0.437043 -0.654288  0.330046  ...   3.0   
359  1.15849 -0.567994  0.230944  0.437043 -0.654288  0.330046  ...   3.0   
359  1.15849 -0.567994  0.230944  0.437043 -0.654288  0.330046  ...   3.0   
359  1.15849 -0.567994  0.230944  0.437043 -0.654288  0.330046  ...   3.0   
359  1.15849 -0.567994  0.230944  0.437043 -0.654288  0.330046  ...   3.0   

     change  first   last    heading                              time  \
0         0  False  False  89.042705  2023-01-16 17:25:52.120000+00:00   
0         0  False  False  89.042705  2023-01-16 17:25:52.120000+00:00   
0         0  False  False  89.042705  2023-01-16 17:25:52.120000+00:00   
0         0  False  False  89.042705  2023-01-16 17:25:52.120000+00:00   
0         0  False  False  89.042705  2023-01-16 17:25:52.120000+00:00   
..      ...    ...    ...        ...                               ...   
359       0  False   True   0.000000  2023-01-16 17:31:08.723000+00:00   
359       0  False   True   0.000000  2023-01-16 17:31:08.723000+00:00   
359       0  False   True   0.000000  2023-01-16 17:31:08.723000+00:00   
359       0  False   True   0.000000  2023-01-16 17:31:08.723000+00:00   
359       0  False   True   0.000000  2023-01-16 17:31:08.723000+00:00   

     passID  speed  temperature  density  
0         1    1.1        167.5        4  
0         1    1.1        167.5        4  
0         1    1.1        167.5        4  
0         1    1.1        167.5        4  
0         1    1.1        167.5        4  
..      ...    ...          ...      ...  
359       4    1.1        167.5        2  
359       4    1.1        167.5        2  
359       4    1.1        167.5        2  
359       4    1.1        167.5        2  
359       4    1.1        167.5        2  

[10164 rows x 25 columns]

In [15]:
lon_min = full_data_projected.longitude.min()
lon_max = full_data_projected.longitude.max()
lat_min = full_data_projected.longitude.min()
lat_max = full_data_projected.longitude.max()

nHexBins_lat = int(
    (lat_max - lat_min) * 3600 * 80 / 2
)  
nHexBins_lon = int(
    (lon_max - lon_min) * 3600 * 80 / 2
    
)  

nHexBins=max(nHexBins_lon,nHexBins_lat)
nHexBins

7

In [16]:
def getLastValue(hexBin):
#     print (hexBin)
    return hexBin[-1]

In [32]:
coverageFig = {}
# Coverage map colored by pass count
coverageFig["passes"] = ff.create_hexbin_mapbox(
    data_frame=full_data_projected,
    lat="latitude",
    lon="longitude",
    labels={"color": "Number of Passes"},
    nx_hexagon=nHexBins,
    agg_func=getLastValue,
    show_original_data=True,
    color="density",
    zoom=18,
)

coverageFig

{'passes': Figure({
     'data': [{'coloraxis': 'coloraxis',
               'customdata': array([[4.0, '-1.6870763123695685,0.6671710130044683', 0],
                                    [3.0, '-1.6870763123695685,0.6671712519187006', 0],
                                    [0.0, '-1.6870763123695685,0.6671714908329329', 0],
                                    ...,
                                    [2.0, '-1.6870754157777923,0.6671876175436132', 0],
                                    [0.0, '-1.6870754157777923,0.6671878564578455', 0],
                                    [4.0, '-1.6870754157777923,0.6671880953720778', 0]], dtype=object),
               'geojson': {'features': [{'geometry': {'coordinates': [[[-96.6623524
                                                                      1527079, 35.66
                                                                      9994473247655]
                                                                      , [-96.6623484
               

In [33]:
len(coverageFig["passes"].data[0].geojson["features"]), len(coverageFig["passes"].data[0].customdata)

(1103, 906)

In [34]:
# vertex_point=coverageFig["passes"].data[0].geojson["features"][0]["geometry"]['coordinates'][0]
# vertex_point=vertex_point
# vertex_point

In [52]:
vertices_list_c=[coverageFig["passes"].data[0].geojson["features"][i]["geometry"]['coordinates'][0] 
                 for i in range (len(coverageFig["passes"].data[0].geojson["features"]))]
vertices_collection={coverageFig["passes"].data[0].geojson["features"][i]["id"]:
                      coverageFig["passes"].data[0].geojson["features"][i]["geometry"]['coordinates'][0]
                     for i in range (len(coverageFig["passes"].data[0].geojson["features"]))}
vertex_true_1=vertices_collection[coverageFig["passes"].data[0].customdata[0][1]]
vertex_true_1

[[-96.66235241527079, 35.669994473247655],
 [-96.6623484636612, 35.66999632668299],
 [-96.6623484636612, 35.67000003355355],
 [-96.66235241527079, 35.670001886988764],
 [-96.66235636688039, 35.67000003355355],
 [-96.66235636688039, 35.66999632668299],
 [-96.66235241527079, 35.669994473247655]]

In [64]:
# points=np.array(full_data_projected[["longitude","latitude"]])
# m_vertex_path=[mpltPath.Path(x) for x in vertices_list_c]
# inside=[x.contains_points(points) for x in m_vertex_path]
# [[i for i in p if i ==True] for p in inside]

In [62]:
def is_inside(path,point):
#     print(path.contains_point(point))
    return path.contains_point(point)

def get_data_inside(dataframe,vertices):
    vertex_path=mpltPath.Path(vertices)
    ret_data=dataframe[["longitude","latitude"]].apply(lambda x: is_inside(vertex_path,[x[0],x[1]]),axis=1)
#     ret_data = vertex_path.contains_points(np.array(dataframe[["latitude","longitude"]]))
    if not dataframe[ret_data].empty:
        return dataframe[ret_data]
    
return_val=[get_data_inside(full_data_projected[["latitude","longitude","density","passID"]],i) for i in val]

In [63]:
return_val

[   latitude  longitude  density  passID
 0     35.67 -96.662342        4       3
 0     35.67 -96.662342        4       3,
     latitude  longitude  density  passID
 1  35.670005 -96.662341        1       2
 1  35.670005 -96.662344        1       2
 1  35.670005 -96.662341        1       2
 2  35.670007 -96.662341        0       2
 2  35.670007 -96.662341        0       2
 2  35.670007 -96.662344        0       2
 2  35.670004 -96.662342        0       3
 2  35.670004 -96.662342        0       3
 3  35.670007 -96.662342        2       3
 3  35.670007 -96.662342        2       3
 4  35.670009 -96.662342        2       3
 4  35.670009 -96.662342        2       3
 0  35.670007 -96.662343        4       4
 0  35.670007 -96.662340        4       4,
     latitude  longitude  density  passID
 5  35.670014 -96.662341        2       2
 5  35.670014 -96.662344        2       2
 5  35.670014 -96.662341        2       2
 6  35.670016 -96.662341        3       2
 6  35.670016 -96.662341        3  

In [76]:
def get_data_inside(dataframe,vertices_k_v):
#     print(vertices_k_v)
    vertex_path=mpltPath.Path(vertices_k_v[1])
    ret_data = vertex_path.contains_points(np.array(dataframe[["longitude","latitude"]]))
    if not dataframe[ret_data].empty:
#         print(dataframe[ret_data])
        return {vertices_k_v[0]: dataframe[ret_data]}
    
get_data=[get_data_inside(df,(vertex_point,vertices_collection[vertex_point])) for vertex_point in vertices_collection]

[{'-1.6870763123695685,0.6671710130044683':    Unnamed: 0.1  Unnamed: 0                         timestamp  total_power  \
  0             0           0  2023-01-16 17:29:06.120000+00:00        100.0   
  0             0           0  2023-01-16 17:29:06.120000+00:00        100.0   
  
      p0   p1   p2        p3   p4   p5  ...  prev  change  first   last  \
  0 -2.0  2.0  2.0  0.538652  2.0  2.0  ...   NaN       0  False  False   
  0 -2.0  2.0  2.0  0.538652  2.0  2.0  ...   NaN       0  False  False   
  
       heading                              time  passID  speed  temperature  \
  0  89.061992  2023-01-16 17:29:06.120000+00:00       3    1.1        167.5   
  0  89.061992  2023-01-16 17:29:06.120000+00:00       3    1.1        167.5   
  
     density  
  0        4  
  0        4  
  
  [2 rows x 25 columns]},
 {'-1.6870763123695685,0.6671712519187006':    Unnamed: 0.1  Unnamed: 0                         timestamp  total_power  \
  2             2           2  2023-01-16 17:27:

In [46]:
df[["latitude","longitude"]]

latitude  longitude
0    35.670014 -96.662317
0    35.670014 -96.662327
0    35.670014 -96.662310
0    35.670014 -96.662314
0    35.670014 -96.662324
..         ...        ...
359  35.670790 -96.662319
359  35.670784 -96.662319
359  35.670792 -96.662319
359  35.670787 -96.662319
359  35.670778 -96.662319

[10164 rows x 2 columns]

In [43]:
import math

df=full_data_projected.copy(deep=True)

vertex_point=[[-96.66234200000004, 35.670057540900615],
 [-96.66233928571432, 35.6700588139892],
 [-96.66233928571432, 35.67006136016635],
 [-96.66234200000004, 35.67006263325489],
 [-96.66234471428577, 35.67006136016635],
 [-96.66234471428577, 35.6700588139892],
 [-96.66234200000004, 35.670057540900615]]

path = mpltPath.Path(vertex_point)
inside2 = path.contains_point([-96.66234200000004, 35.670060])
inside2

is_inside(path,[-96.66234200000004, 35.670060])

True